<center><h2>Continuous Wavelet Transform </h2></center>
<p>
The wavelet transform of a time signal $y(t)$,
    $$
Y(s, \tau) = \int_{-\infty}^{+\infty} dt\,
\psi_{s,\tau}^*(t) y(t),
 $$
uses a basis  $\psi_{s,\tau}(t)$ that is localized in time  and contains a small range of frequencies.
We start with the mother wavelet
\begin{align}
\Psi (t) = \sin(8t) e^{-t^2/2},
\end{align}
and form wavelet  basis functions 
$$
\psi_{s,\tau}(t) = \frac{1}{\sqrt{s}}
\Psi\left(\frac{t-\tau}{s}\right) = \frac{1}{\sqrt{s}} \sin\left[
\frac{8(t-\tau)}{s}\right]\, e^{-{(t-\tau)^2} /{2s^2}}.
 $$
 The transform is applied to:
 $$
y(t) = \begin{cases}
 \sin 2\pi t, & \hbox{for } \ 0 \leq t \leq 2,\\[3pt]
 5\sin 2\pi t + 10\sin 4\pi t , & \hbox{for } \ 2 \leq t \leq 8,\\[3pt]
 2.5\sin 2\pi t + 6\sin 4\pi t + 10\sin 6\pi t, &\hbox{for }\ 8 \leq t \leq 12.
\end{cases}
 $$
 
 Based on a program written by Written by Zlatko Dimcovic.

In [ ]:
""" From "COMPUTATIONAL PHYSICS" & "COMPUTER PROBLEMS in PHYSICS"
    by RH Landau, MJ Paez, and CC Bordeianu (deceased).
    Copyright R Landau, Oregon State Unv, MJ Paez, Univ Antioquia, 
    C Bordeianu, Univ Bucharest, 2021. 
    Please respect copyright & acknowledge our work."""

# ContWavelet.ipynb  Continuous Wavelet Transform. Written by Zlatko Dimcovic

from vpython import *
import numpy as np

N = 240
transfgr = canvas(x=0,y=0,width=600,height=200, title='Transform, not normalized')
transf   = curve(x=list(range(0,90)),display=transfgr,color=color.cyan)
wavlgr   = canvas(x=0,y=200,width=600,height=200,
                title='Morlet Wavelet at different scales, up to s=12.0')
wavelet  = curve(x=list(range(0,N)),display=wavlgr,color=color.yellow)
invtrgr  = canvas(x=0,y=400,width=600,height=200,
                title='Inverse TF, not normalized')
invtr    = curve(x=list(range(0,N)),display=invtrgr,color=color.green)
wvlabel  = label(pos=vec(0, -50,0), text='s=', box=0,display=wavlgr)
iT       = 0.0
fT       = 12.0
W        = fT - iT                           # i,f times
h        = W/N;                              # Steps
noPtsSig = N
noS      = 30    
noTau    = 90                           # of pts
iTau     = 0.
iS       = 0.1
tau      = iTau
s        = iS

''' Need *very* small s steps for high-frequency, but only if s is small
Thus increment s by multiplying by number close enough to 1 '''

dTau = W/noTau
dS   = (W/iS)**(1./noS)
sig  = np.zeros((noPtsSig),float)                                   # Signal
Y    = np.zeros((noS,noTau),float)                               # Transform
maxY = 0.001;

def signal(noPtsSig, y):                                     # The signal
    t = 0.0
    hs = W / noPtsSig
    t1 = W/6.
    t2 = 4.*W/6.
    for i in range(0,noPtsSig):  
        if   t >= iT and t <= t1: y[i] = sin(2*pi*t)
        elif t >= t1 and t <= t2:	y[i] = 5.*sin(2*pi*t) +10.*sin(4*pi*t);
        elif t >= t2 and t <= fT: y[i] = 2.5*sin(2*pi*t)+6.*sin(4*pi*t)+10.*sin(6*pi*t)
        else:
            print("In signal(...) : t out of range.")
            sys.exit(1)
        t += hs    
signal(noPtsSig, sig)

def morlet(t, s, tau):                                           # Mother
     T = (t-tau)/s
     return sin(8*T) * exp(-T*T/2.)
 
def transform(s, tau, sig, j):            
    integral = 0.
    t = 0.0                             # "initial time" = class variable
    if j%2==0:   wvlabel.text = 's=%5.3f' %s
    wavelet.clear()
    for i in range(0,len(sig)):
         t +=h
         rate(1500)
         yy=morlet(t,s,tau)
         wavelet.append(pos=vec(110.0/3*t-240,40.0*yy,0))
         integral += sig[i]*yy*h
         output=integral/sqrt(s) 
         wavelet.visible=True   
    return output

def invTransform(t,Y):        # given the transform (from previous steps)
    s = iS                                     # computes original signal
    tau = iTau
    recSig_t = 0                 
    for i in range (0,noS):
        s  *= dS                 
        tau = iTau
        for j in range (0,noTau):
            tau      += dTau
            recSig_t += dTau*dS *(s**(-1.5))* Y[i,j] * morlet(t,s,tau)
    return recSig_t
    
print("working, finding transform")
for i in range( 0, noS):
    s  *= dS                                                  # Scaling s
    tau = 0.0
    transf.clear()
    for j in range(0,noTau):
         rate(1500)
         tau        += dTau                                 # Translation
         Y[i,j]      = transform(s, tau, sig,i)
         transf.append(pos=vec(40./3.0*tau-80, 4.0*Y[i,j] ,0))
         transf.visible = True        
print("transform found")
print("finding inverse transform")		                       # Inverse TF
recSigData = "recSig.dat"                   
recSig     = np.zeros(len(sig))                            # Same resolution
t   = 0.0;
kco = 0
j   = 0

for rs in range(0, len(recSig)):   			         # with inverse transform
    recSig[rs] = invTransform(t, Y) 			     # find the original signal
    t += h                          		                 # not normalized
    invtr.append(pos =vec( rs*2.0-220, 1.5*recSig[rs],0))
print("nDone")              